In [1]:
import openseespy.opensees as ops
import opstool as opst
from pathlib import Path

In [2]:
ops.wipe()
ops.model("basic", "-ndm", 3, "-ndf", 6)
# 材料参数
E, nu, rho = 2.06e11, 0.3, 7850  # Pa, kg/m3
ops.nDMaterial("ElasticIsotropic", 1, E, nu, rho)
# 薄板纤维截面
secTag = 11
thick = 0.004   # 4mm
ops.section("PlateFiber", secTag, 1, thick)

In [3]:
# 读取GMSH文件
GMSH2OPS = opst.pre.Gmsh2OPS(ndm=3, ndf=6)

mesh_file = Path.cwd() / "street_light.msh"
GMSH2OPS.read_gmsh_file(mesh_file.absolute())

# 根据GMSH文件创建OpenSeesPy节点命令
node_tags = GMSH2OPS.create_node_cmds()

dim_entity_tags = GMSH2OPS.get_dim_entity_tags()
dim_entity_tags_2D = [item for item in dim_entity_tags if item[0] == 2]

# 根据GMSH文件创建OpenSeesPy元素命令
ele_tags_n4 = GMSH2OPS.create_element_cmds(
    ops_ele_type="ASDShellQ4",  # OpenSeesPy 单元类型
    ops_ele_args=[
        secTag
    ],  # 单元额外参数(e.g., section tag)
    dim_entity_tags=dim_entity_tags_2D,
)

# 移除无效网格
removed_node_tags = opst.pre.remove_void_nodes()
print(removed_node_tags)

Info:: 3 Physical Names.
Info:: 640 Nodes; MaxNodeTag 640; MinNodeTag 1.
Info:: 656 Elements; MaxEleTag 656; MinEleTag 1.
Info:: Geometry Information >>>
1314 Entities: 336 Point; 656 Curves; 322 Surfaces; 0 Volumes.

Info:: Physical Groups Information >>>
3 Physical Groups.
Physical Group names: ['bottom_boundary', 'top_boundary', 'tube_surface']

Info:: Mesh Information >>>
640 Nodes; MaxNodeTag 640; MinNodeTag 1.
656 Elements; MaxEleTag 656; MinEleTag 1.



Using ASDShellQ4 - Developed by: Massimo Petracca, Guido Camata, ASDEA Software Technology


Info:: The model has no free nodes!

[]


In [4]:
MODEL_MASS = opst.pre.ModelMass()
MODEL_MASS.add_mass_from_surf(ele_tags=ele_tags_n4, rho=rho, d=thick)
MODEL_MASS.generate_ops_node_mass()
print(MODEL_MASS.get_total_mass())

147.73307579236464


In [5]:
# 获取边界实体标签以创建约束
bottom_boundary_dim_tags = GMSH2OPS.get_boundary_dim_tags(
    physical_group_names="bottom_boundary", include_self=True)
print(bottom_boundary_dim_tags)

top_boundary_dim_tags = GMSH2OPS.get_boundary_dim_tags(
    physical_group_names="top_boundary", include_self=True)
print(top_boundary_dim_tags)

[(0, 1), (0, 2), (0, 3), (0, 4), (0, 5), (0, 6), (0, 7), (0, 8), (0, 9), (0, 10), (0, 11), (0, 12), (0, 13), (0, 14), (0, 15), (0, 16), (1, 1), (1, 2), (1, 3), (1, 4), (1, 5), (1, 6), (1, 7), (1, 8), (1, 9), (1, 10), (1, 11), (1, 12), (1, 13), (1, 14), (1, 15), (1, 16)]
[(0, 321), (0, 322), (0, 323), (0, 324), (0, 325), (0, 326), (0, 327), (0, 328), (0, 329), (0, 330), (0, 331), (0, 332), (0, 333), (0, 334), (0, 335), (0, 336), (1, 321), (1, 322), (1, 323), (1, 324), (1, 325), (1, 326), (1, 327), (1, 328), (1, 329), (1, 330), (1, 331), (1, 332), (1, 333), (1, 334), (1, 335), (1, 336)]


In [ ]:
# 约束底面
fix_ntags = GMSH2OPS.create_fix_cmds(dim_entity_tags=bottom_boundary_dim_tags, dofs=[1] * 6)

# 约束顶面（连接一个质量点）
light_tag = 1000000
ops.node(light_tag, 1.2, 0, 9)
ops.mass(light_tag, 30,30,30,0,0,0)  # 质量30kg
transfTag = 6666
ops.geomTransf('Linear',transfTag,0,0,1)
eleTag = 100000
# 在节点和灯的单元之间创建刚臂
for dim, tag in top_boundary_dim_tags:
    if dim == 0:
        # ops.rigidLink('beam', light_tag, tag)
        ops.element('elasticBeamColumn', eleTag, light_tag, tag,50,3.25e7,1.25e7,100,100,100,transfTag)
        eleTag+=1

In [7]:
opst.vis.pyvista.set_plot_props(notebook=True)
opst.vis.pyvista.plot_model(show_outline=True).show(jupyter_backend='html')

OPSTOOL ::  Model data has been saved to _OPSTOOL_ODB/ModelData-None.nc!

EmbeddableWidget(value='<iframe srcdoc="<!DOCTYPE html>\n<html>\n  <head>\n    <meta http-equiv=&quot;Content-…

In [8]:
# ====== 定义重力荷载 ====== #

# 创建带有线性时间序列的Plain荷载模式
ops.timeSeries('Linear', 1)
ops.pattern('Plain', 1, 1)

g = 9.81
MODEL_MASS.generate_ops_gravity_load(direction="z", factor=-g)


# ====== 静力分析设置 ====== #
Nsteps = 10
ops.system('BandGeneral')   # 求解器类型，BandGeneral适用于带状矩阵，如梁柱结构
ops.constraints('Transformation')  # 约束处理方法，Transformation，适用于大多数问题
ops.numberer('RCM')  # 节点编号方法，RCM (Reverse Cuthill-McKee)算法，可以减少带宽
ops.test('NormDispIncr', 1.0e-12, 15, 3)  # 收敛测试:位移增量范数,容差1.0e-12,最大迭代数15
ops.algorithm('Newton')  # 解算法，Newton-Raphson法，适用于大多数非线性问题
ops.integrator('LoadControl', 1 / Nsteps) # Nsteps与步长的乘积一定要为1，代表施加一倍荷载，乘积为2代表施加两倍荷载
ops.analysis('Static')

# 静力分析循环
for i in range(Nsteps):
    ok = ops.analyze(1)

ops.loadConst('-time', 0.0)
print("静力分析完成")

静力分析完成


In [9]:
opst.post.save_eigen_data(odb_tag="eigen", mode_tag=60)

fig = opst.vis.plotly.plot_eigen(mode_tags=9, odb_tag="eigen", subplots=False)
fig.show()

Using DomainModalProperties - Developed by: Massimo Petracca, Guido Camata, ASDEA Software Technology


OPSTOOL ::  Eigen data has been saved to _OPSTOOL_ODB/EigenData-eigen.nc!

OPSTOOL ::  Loading eigen data from _OPSTOOL_ODB/EigenData-eigen.nc ...

In [10]:
modal_props, eigen_vectors = opst.post.get_eigen_data(odb_tag="eigen")
modal_props = modal_props.to_pandas()
print(modal_props.head())

OPSTOOL ::  Loading eigen data from _OPSTOOL_ODB/EigenData-eigen.nc ...

Properties  eigenLambda  eigenOmega  eigenFrequency  eigenPeriod  \
modeTags                                                           
1             63.212623    7.950637        1.265383     0.790274   
2             63.224506    7.951384        1.265502     0.790200   
3           1698.247666   41.209801        6.558743     0.152468   
4           1847.250917   42.979657        6.840425     0.146190   
5           5448.710138   73.815379       11.748082     0.085120   

Properties  partiFactorMX  partiFactorMY  partiFactorRMZ  partiFactorMZ  \
modeTags                                                                  
1            3.824526e-03  -1.388046e+01   -2.522610e+00  -2.033571e-04   
2           -1.383199e+01  -3.837979e-03   -6.974675e-04   7.353693e-01   
3            7.512452e-07  -6.685378e+00    5.474531e+00   3.386833e-07   
4            7.255640e+00   6.032181e-07   -5.290134e-07   3.458669e+00   
5            8.080771e-08  -5.003876e+00   -2.192723e+00  -6.072146e-08  

In [ ]:
print(modal_props.loc[[1,2,3,4,5,10,20,30,40], "eigenPeriod"])

In [11]:
# 地震动分析
# 删除旧的分析
ops.wipeAnalysis()

# 修改分析设置以适应地震分析
ops.system('BandGeneral')
ops.constraints('Plain')
ops.test('NormDispIncr', 1.0e-12,  10)
ops.algorithm('Newton')
ops.numberer('RCM')
ops.integrator('Newmark',  0.5,  0.25)
ops.analysis('Transient')

In [12]:
# 读取地震动记录
from pathlib import Path
# 将earthquakerecord.txt文件放在同一目录下即可
filepath = Path.cwd().parent / 'Case1_Earthquake_Simple_Supported_Bridge' / 'earthquakerecord.txt'
print(f"地震记录文件路径：{filepath.absolute()}")
# 设置时间序列
nsteps,dt = 6062,0.01
ts_tag = 3
ops.timeSeries('Path', ts_tag, '-filePath', str(filepath), '-dt', dt, '-factor', g)
# 创建地震动荷载模式
axis = 1    # 地震动输入方向
ops.pattern('UniformExcitation', 2, axis, '-accel', ts_tag)

地震记录文件路径：d:\python\openseespy_zh_totorial\Case1_Earthquake_Simple_Supported_Bridge\earthquakerecord.txt


In [13]:
from IPython.display import clear_output
# SmartAnalyze可以控制自动更换分析方法，积分步长等等设置，非常方便，具体查看opstool文档，这里简单演示，不调整参数
analysis = opst.anlys.SmartAnalyze(analysis_type="Transient",)
ODB = opst.post.CreateODB(odb_tag=2)
segs = analysis.transient_split(nsteps)
for seg in segs:
    clear_output(wait=True)  # 清除之前的输出，不是分析必要的，只是为了看起来更美观
    analysis.TransientAnalyze(dt)   # 分析一个dt
    ODB.fetch_response_step()
        
# 保存地震分析结果(zlib可以压缩文件大小)
ODB.save_response(zlib=True)

>>> SmartAnalyze: Successfully finished! Time consumption: 1738.987 s.

OPSTOOL ::  All responses data with odb_tag = 2 saved in _OPSTOOL_ODB/RespStepData-2.nc!

In [ ]:
# 想不想知道地震过程中结构的受力情况？(简单看看Opstool记录的结果)
opsvis.set_plot_props(cmap="jet", point_size=2.0)
opsvis.set_plot_colors(frame="black")


fig = opsvis.plot_frame_responses(
    odb_tag=2,
    slides=True,
    resp_type="basicForces",
    resp_dof="Mz",
    scale=-3.0,
    show_values=True,
    line_width=5,
)

fig.show()